In [1]:
import xarray as xr
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
import glob
import os

def process_multiple_merra2_files_washington(directory_path):
    # Washington state boundaries
    WA_LAT_MIN, WA_LAT_MAX = 45.5, 49.0
    WA_LON_MIN, WA_LON_MAX = -124.8, -116.9
    
    # Get all MERRA2 files in the directory
    file_pattern = os.path.join(directory_path, "MERRA2_400.tavg1_2d_aer_Nx.*")
    files = sorted(glob.glob(file_pattern))
    
    print(f"Found {len(files)} files to process")
    
    # Lists to store DataFrames
    hourly_dfs = []
    daily_dfs = []
    
    for idx, file in enumerate(files, 1):
        print(f"Processing file {idx}/{len(files)}: {os.path.basename(file)}")
        
        try:
            # Open the NetCDF file using xarray
            ds = xr.open_dataset(file)
            
            # Extract latitude and longitude
            lats = ds['lat'].values
            lons = ds['lon'].values
            
            # Filter coordinates for Washington state
            wa_lat_mask = (lats >= WA_LAT_MIN) & (lats <= WA_LAT_MAX)
            wa_lon_mask = (lons >= WA_LON_MIN) & (lons <= WA_LON_MAX)
            
            wa_lats = lats[wa_lat_mask]
            wa_lons = lons[wa_lon_mask]
            
            # Extract TOTANGSTR values for Washington only
            DUSMASS25 = ds['DUSMASS25'].values[:, wa_lat_mask, :][:, :, wa_lon_mask]
            
            # Extract time and convert to UTC
            times = ds['time'].values
            time_utc = pd.to_datetime(times)
            
            # Create a list for Washington coordinates
            coords = []
            for lat in wa_lats:
                for lon in wa_lons:
                    coords.append([lat, lon])
            
            # Create a DataFrame with coordinates as index
            df = pd.DataFrame(index=pd.MultiIndex.from_tuples(coords, names=['latitude', 'longitude']))
            
            # Add time data
            for t_idx, timestamp in enumerate(time_utc):
                time_data = []
                for lat_idx, lat in enumerate(wa_lats):
                    for lon_idx, lon in enumerate(wa_lons):
                        time_data.append(DUSMASS25[t_idx, lat_idx, lon_idx])
                df[timestamp] = time_data
            
            # Reset index to convert MultiIndex to columns
            df = df.reset_index()
            
            # Calculate daily averages
            time_columns = df.columns[2:]  # Skip latitude and longitude columns
            daily_df = pd.DataFrame()
            daily_df['latitude'] = df['latitude']
            daily_df['longitude'] = df['longitude']
            
            # Group timestamps by date and calculate mean
            dates = pd.to_datetime(time_columns).date
            unique_dates = list(set(dates))
            for date in unique_dates:
                date_cols = [col for col, d in zip(time_columns, dates) if d == date]
                daily_df[date] = df[date_cols].mean(axis=1)
            
            # Append to lists
            hourly_dfs.append(df)
            daily_dfs.append(daily_df)
            
            # Close the dataset
            ds.close()
            
        except Exception as e:
            print(f"Error processing file {file}: {str(e)}")
            continue
    
    # Combine all DataFrames
    print("Combining all data...")
    
    # For hourly data
    combined_hourly = hourly_dfs[0].copy()
    for df in hourly_dfs[1:]:
        # Only append the time columns, not lat/lon
        new_columns = df.columns[2:]
        combined_hourly[new_columns] = df[new_columns]
    
    # For daily data
    combined_daily = daily_dfs[0].copy()
    for df in daily_dfs[1:]:
        # Only append the date columns, not lat/lon
        new_columns = df.columns[2:]
        combined_daily[new_columns] = df[new_columns]
    
    # Sort columns (except first two lat/lon columns)
    combined_hourly = pd.concat([
        combined_hourly.iloc[:, :2],
        combined_hourly.iloc[:, 2:].sort_index(axis=1)
    ], axis=1)
    
    combined_daily = pd.concat([
        combined_daily.iloc[:, :2],
        combined_daily.iloc[:, 2:].sort_index(axis=1)
    ], axis=1)
    
    return combined_hourly, combined_daily

# Usage example
directory_path = "Downloads/M2T1NXAER_5.12.4-20250117_084759"  # Replace with your directory path
hourly_df, daily_df = process_multiple_merra2_files_washington(directory_path)

# Save to CSV
print("Saving results to CSV files...")
hourly_df.to_csv("washington_merra2_dustPM2.5_hourly_data.csv", index=False)
daily_df.to_csv("washington_merra2_dustPM2.5_daily_data.csv", index=False)

# Print information about the results
print("\nHourly data shape:", hourly_df.shape)
print("Daily data shape:", daily_df.shape)
print("\nNumber of grid points:", len(hourly_df))
print("\nSample of hourly data:")
print(hourly_df.head())
print("\nSample of daily data:")
print(daily_df.head())

# Print coordinate ranges to verify
print("\nLatitude range:", hourly_df['latitude'].min(), "to", hourly_df['latitude'].max())
print("Longitude range:", hourly_df['longitude'].min(), "to", hourly_df['longitude'].max())


Found 365 files to process
Processing file 1/365: MERRA2_400.tavg1_2d_aer_Nx.20160101.nc4
Processing file 2/365: MERRA2_400.tavg1_2d_aer_Nx.20160102.nc4
Processing file 3/365: MERRA2_400.tavg1_2d_aer_Nx.20160103.nc4
Processing file 4/365: MERRA2_400.tavg1_2d_aer_Nx.20160104.nc4
Processing file 5/365: MERRA2_400.tavg1_2d_aer_Nx.20160105.nc4
Processing file 6/365: MERRA2_400.tavg1_2d_aer_Nx.20160106.nc4
Processing file 7/365: MERRA2_400.tavg1_2d_aer_Nx.20160107.nc4
Processing file 8/365: MERRA2_400.tavg1_2d_aer_Nx.20160108.nc4
Processing file 9/365: MERRA2_400.tavg1_2d_aer_Nx.20160109.nc4
Processing file 10/365: MERRA2_400.tavg1_2d_aer_Nx.20160110.nc4
Processing file 11/365: MERRA2_400.tavg1_2d_aer_Nx.20160111.nc4
Processing file 12/365: MERRA2_400.tavg1_2d_aer_Nx.20160112.nc4
Processing file 13/365: MERRA2_400.tavg1_2d_aer_Nx.20160113.nc4
Processing file 14/365: MERRA2_400.tavg1_2d_aer_Nx.20160114.nc4
Processing file 15/365: MERRA2_400.tavg1_2d_aer_Nx.20160115.nc4
Processing file 16/365

C:\Users\priom\AppData\Local\Temp\ipykernel_36780\2751738430.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  combined_hourly[new_columns] = df[new_columns]
C:\Users\priom\AppData\Local\Temp\ipykernel_36780\2751738430.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  combined_hourly[new_columns] = df[new_columns]
C:\Users\priom\AppData\Local\Temp\ipykernel_36780\2751738430.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performa

Saving results to CSV files...

Hourly data shape: (96, 8738)
Daily data shape: (96, 366)

Number of grid points: 96

Sample of hourly data:
   latitude  longitude  2016-01-01 00:30:00  2016-01-01 01:30:00  \
0      45.5   -124.375         2.123102e-10         2.151524e-10   
1      45.5   -123.750         2.056595e-10         2.074785e-10   
2      45.5   -123.125         2.091838e-10         2.115144e-10   
3      45.5   -122.500         2.102638e-10         2.144703e-10   
4      45.5   -121.875         2.139018e-10         2.186767e-10   

   2016-01-01 02:30:00  2016-01-01 03:30:00  2016-01-01 04:30:00  \
0         2.236221e-10         2.324896e-10         2.377192e-10   
1         2.111733e-10         2.146976e-10         2.182787e-10   
2         2.146976e-10         2.176535e-10         2.196998e-10   
3         2.190177e-10         2.223146e-10         2.216893e-10   
4         2.226557e-10         2.250431e-10         2.224851e-10   

   2016-01-01 05:30:00  2016-01-01 06:30:

In [2]:
import xarray as xr
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
import glob
import os

def process_multiple_merra2_files_washington(directory_path):
    # Washington state boundaries
    WA_LAT_MIN, WA_LAT_MAX = 45.5, 49.0
    WA_LON_MIN, WA_LON_MAX = -124.8, -116.9
    
    # Get all MERRA2 files in the directory
    file_pattern = os.path.join(directory_path, "MERRA2_400.tavg1_2d_aer_Nx.*")
    files = sorted(glob.glob(file_pattern))
    
    print(f"Found {len(files)} files to process")
    
    # Lists to store DataFrames
    hourly_dfs = []
    daily_dfs = []
    
    for idx, file in enumerate(files, 1):
        print(f"Processing file {idx}/{len(files)}: {os.path.basename(file)}")
        
        try:
            # Open the NetCDF file using xarray
            ds = xr.open_dataset(file)
            
            # Extract latitude and longitude
            lats = ds['lat'].values
            lons = ds['lon'].values
            
            # Filter coordinates for Washington state
            wa_lat_mask = (lats >= WA_LAT_MIN) & (lats <= WA_LAT_MAX)
            wa_lon_mask = (lons >= WA_LON_MIN) & (lons <= WA_LON_MAX)
            
            wa_lats = lats[wa_lat_mask]
            wa_lons = lons[wa_lon_mask]
            
            # Extract TOTANGSTR values for Washington only
            DUSCAT25 = ds['DUSCAT25'].values[:, wa_lat_mask, :][:, :, wa_lon_mask]
            
            # Extract time and convert to UTC
            times = ds['time'].values
            time_utc = pd.to_datetime(times)
            
            # Create a list for Washington coordinates
            coords = []
            for lat in wa_lats:
                for lon in wa_lons:
                    coords.append([lat, lon])
            
            # Create a DataFrame with coordinates as index
            df = pd.DataFrame(index=pd.MultiIndex.from_tuples(coords, names=['latitude', 'longitude']))
            
            # Add time data
            for t_idx, timestamp in enumerate(time_utc):
                time_data = []
                for lat_idx, lat in enumerate(wa_lats):
                    for lon_idx, lon in enumerate(wa_lons):
                        time_data.append(DUSCAT25[t_idx, lat_idx, lon_idx])
                df[timestamp] = time_data
            
            # Reset index to convert MultiIndex to columns
            df = df.reset_index()
            
            # Calculate daily averages
            time_columns = df.columns[2:]  # Skip latitude and longitude columns
            daily_df = pd.DataFrame()
            daily_df['latitude'] = df['latitude']
            daily_df['longitude'] = df['longitude']
            
            # Group timestamps by date and calculate mean
            dates = pd.to_datetime(time_columns).date
            unique_dates = list(set(dates))
            for date in unique_dates:
                date_cols = [col for col, d in zip(time_columns, dates) if d == date]
                daily_df[date] = df[date_cols].mean(axis=1)
            
            # Append to lists
            hourly_dfs.append(df)
            daily_dfs.append(daily_df)
            
            # Close the dataset
            ds.close()
            
        except Exception as e:
            print(f"Error processing file {file}: {str(e)}")
            continue
    
    # Combine all DataFrames
    print("Combining all data...")
    
    # For hourly data
    combined_hourly = hourly_dfs[0].copy()
    for df in hourly_dfs[1:]:
        # Only append the time columns, not lat/lon
        new_columns = df.columns[2:]
        combined_hourly[new_columns] = df[new_columns]
    
    # For daily data
    combined_daily = daily_dfs[0].copy()
    for df in daily_dfs[1:]:
        # Only append the date columns, not lat/lon
        new_columns = df.columns[2:]
        combined_daily[new_columns] = df[new_columns]
    
    # Sort columns (except first two lat/lon columns)
    combined_hourly = pd.concat([
        combined_hourly.iloc[:, :2],
        combined_hourly.iloc[:, 2:].sort_index(axis=1)
    ], axis=1)
    
    combined_daily = pd.concat([
        combined_daily.iloc[:, :2],
        combined_daily.iloc[:, 2:].sort_index(axis=1)
    ], axis=1)
    
    return combined_hourly, combined_daily

# Usage example
directory_path = "Downloads/M2T1NXAER_5.12.4-20250117_084759"  # Replace with your directory path
hourly_df, daily_df = process_multiple_merra2_files_washington(directory_path)

# Save to CSV
print("Saving results to CSV files...")
hourly_df.to_csv("washington_merra2_dust550PM2.5_hourly_data.csv", index=False)
daily_df.to_csv("washington_merra2_dust550PM2.5_daily_data.csv", index=False)

# Print information about the results
print("\nHourly data shape:", hourly_df.shape)
print("Daily data shape:", daily_df.shape)
print("\nNumber of grid points:", len(hourly_df))
print("\nSample of hourly data:")
print(hourly_df.head())
print("\nSample of daily data:")
print(daily_df.head())

# Print coordinate ranges to verify
print("\nLatitude range:", hourly_df['latitude'].min(), "to", hourly_df['latitude'].max())
print("Longitude range:", hourly_df['longitude'].min(), "to", hourly_df['longitude'].max())


Found 365 files to process
Processing file 1/365: MERRA2_400.tavg1_2d_aer_Nx.20160101.nc4
Processing file 2/365: MERRA2_400.tavg1_2d_aer_Nx.20160102.nc4
Processing file 3/365: MERRA2_400.tavg1_2d_aer_Nx.20160103.nc4
Processing file 4/365: MERRA2_400.tavg1_2d_aer_Nx.20160104.nc4
Processing file 5/365: MERRA2_400.tavg1_2d_aer_Nx.20160105.nc4
Processing file 6/365: MERRA2_400.tavg1_2d_aer_Nx.20160106.nc4
Processing file 7/365: MERRA2_400.tavg1_2d_aer_Nx.20160107.nc4
Processing file 8/365: MERRA2_400.tavg1_2d_aer_Nx.20160108.nc4
Processing file 9/365: MERRA2_400.tavg1_2d_aer_Nx.20160109.nc4
Processing file 10/365: MERRA2_400.tavg1_2d_aer_Nx.20160110.nc4
Processing file 11/365: MERRA2_400.tavg1_2d_aer_Nx.20160111.nc4
Processing file 12/365: MERRA2_400.tavg1_2d_aer_Nx.20160112.nc4
Processing file 13/365: MERRA2_400.tavg1_2d_aer_Nx.20160113.nc4
Processing file 14/365: MERRA2_400.tavg1_2d_aer_Nx.20160114.nc4
Processing file 15/365: MERRA2_400.tavg1_2d_aer_Nx.20160115.nc4
Processing file 16/365

C:\Users\priom\AppData\Local\Temp\ipykernel_36780\3510118296.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  combined_hourly[new_columns] = df[new_columns]
C:\Users\priom\AppData\Local\Temp\ipykernel_36780\3510118296.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  combined_hourly[new_columns] = df[new_columns]
C:\Users\priom\AppData\Local\Temp\ipykernel_36780\3510118296.py:100: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performa

Saving results to CSV files...

Hourly data shape: (96, 8738)
Daily data shape: (96, 366)

Number of grid points: 96

Sample of hourly data:
   latitude  longitude  2016-01-01 00:30:00  2016-01-01 01:30:00  \
0      45.5   -124.375             0.002219             0.002241   
1      45.5   -123.750             0.002154             0.002179   
2      45.5   -123.125             0.002172             0.002183   
3      45.5   -122.500             0.002162             0.002139   
4      45.5   -121.875             0.002013             0.001983   

   2016-01-01 02:30:00  2016-01-01 03:30:00  2016-01-01 04:30:00  \
0             0.002270             0.002264             0.002218   
1             0.002179             0.002140             0.002074   
2             0.002153             0.002103             0.002030   
3             0.002109             0.002057             0.001994   
4             0.001951             0.001904             0.001859   

   2016-01-01 05:30:00  2016-01-01 06:30: